In [1]:
import pulp
import numpy as np

def MILP_EV_real_time_scheduling(pile_data):
    problem = pulp.LpProblem("Battery_Charging", pulp.LpMinimize)

    T_cur = pile_data['T_cur']
    soc_max  = 0.95
    soc_min  = 0.2

    Pc  = pulp.LpVariable.dicts("P_c", [(p, t) for p in pile_data['pile_list'] for t in range(T_cur,96)], 0, cat="Continuous",)
    Pd  = pulp.LpVariable.dicts("P_d", [(p, t) for p in pile_data['pile_list'] for t in range(T_cur,96)], 0, cat="Continuous",)
    Ac  = pulp.LpVariable.dicts("a_c", [(p, t) for p in pile_data['pile_list'] for t in range(T_cur,96)], cat="Binary",)
    Ad  = pulp.LpVariable.dicts("a_d", [(p, t) for p in pile_data['pile_list'] for t in range(T_cur,96)], cat="Binary",)
    soc = pulp.LpVariable.dicts("soc", [(p, t) for p in pile_data['pile_list'] for t in range(T_cur,97)], cat="Continuous")
    
    for p in pile_data['pile_list']:
        problem += soc[(p, T_cur)] == pile_data['SOC'][p]
        for t in range(pile_data['T_cur'], 96):
            problem += Pc[(p, t)] <= Ac[(p, t)]*pile_data['P_max'][p]
            problem += Pd[(p, t)] <= Ad[(p, t)]*pile_data['P_max'][p]
            problem += soc[(p, t+1)] == soc[(p, t)] + Pc[(p, t)]*( 1/ pile_data['BC'][p]/4) - Pd[(p, t)] *( 1/ pile_data['BC'][p]/4)
            problem += soc[(p, t)] <= soc_max
            problem += soc[(p, t)] >= soc_min

        for t in range(pile_data['T_cur'], pile_data['T_d'][p]):
            problem += Ac[(p, t)] + Ad[(p, t)] <= 1
    
        problem += soc[(p, pile_data['T_d'][p])] >= pile_data['SOC_T'][p]
        
        for t in range( pile_data['T_d'][p], 96):
            problem += Ac[(p, t)] + Ad[(p, t)] == 0
    
    for t in range(T_cur, 96):
        problem += pulp.lpSum([ Pc[(p, t)]*(1/pile_data['CE'][p]) - Pd[(p, t)]*(pile_data['CE'][p]) for p in pile_data['pile_list']]) <= pile_data['P_max_station']
        problem += pulp.lpSum([ Pc[(p, t)]*(1/pile_data['CE'][p]) - Pd[(p, t)]*(pile_data['CE'][p]) for p in pile_data['pile_list']]) >= -1*pile_data['P_max_station']

    # target function
    problem += pulp.lpSum( Pc[(p, t)]*(pile_data['price'][t]/pile_data['CE'][p]) - Pd[(p, t)]*(pile_data['price'][t]*pile_data['CE'][p]) for p in pile_data['pile_list'] for t in range(T_cur, 96) )
    
    # preview
    # print(problem)
    
    # get solution
    problem.solve()

    # print("Status:", pulp.LpStatus[problem.status])
    # print("Total Cost:", pulp.value(problem.objective))

    # print(f"---{T_cur}---")
    # for i in pile_data['pile_list']:
    #     print(f" Time 0: SOC {soc[(i, T_cur)].varValue}")
    # for t in range(T_cur,96):
    #     print(f"---{t}---")
    #     for i in pile_data['pile_list']:
    #         print(f"  Charger {i}: Charge {Pc[(i, t)].varValue}, Discharge {Pd[(i, t)].varValue}, Time {t}: SOC {soc[(i, t+1)].varValue}")
            
    return { p : (Pc[(p, T_cur)].varValue - Pd[(p,T_cur)].varValue) for p in pile_data['pile_list']}

def get_pile_data(env):
    return{
            'pile_list' : list(env.charge_power_max.keys()),
            'SOC'       :{ pile: env.pile[pile].SOC          for pile in env.charge_power_max.keys()},
            'SOC_T'     :{ pile: env.pile[pile].SOC_T        for pile in env.charge_power_max.keys()},
            'BC'        :{ pile: env.pile[pile].BC           for pile in env.charge_power_max.keys()},
            'P_max'     :{ pile: env.pile[pile].P_max_charge for pile in env.charge_power_max.keys()},
            'T_d'       :{ pile: env.pile[pile].Td           for pile in env.charge_power_max.keys()},
            'CE'        :{ pile: env.pile[pile].CE           for pile in env.charge_power_max.keys()},
            'T_cur'     : env.T_cur,
            'price'     : env.execute_Pgrid_price,
            'P_max_station' : env.P_max_station
        }

In [2]:
num_of_pile = 150

import time

In [3]:
from MILP_env import StationEnv
import numpy as np
env = StationEnv(mode = "test", N_piles = num_of_pile)
env.seed(0)

env.reset(seed = 1, select_pile = np.random.choice(env.possible_agents))

time_step = env.T_cur
###
start_time = time.time()
###
pile_data = get_pile_data(env)
print(pile_data)
charge_power = MILP_EV_real_time_scheduling(pile_data)
print("==================")

for agent in env.agent_iter():
    obs, reward, termination, truncation, info = env.last()
    if termination or truncation:
        action = None
    else:
        # action = env.action_space(agent).sample()
        action = [charge_power[agent]]

    env.step(action)
    # if time_step > 32:
    #     break
    if time_step != env.T_cur:
        print(pile_data['P_max'])
        pile_data = get_pile_data(env)
        print("==================")
        print(pile_data)
        charge_power = MILP_EV_real_time_scheduling(pile_data)
        time_step = env.T_cur

###
end_time = time.time()
execution_time = end_time - start_time
print("程式執行時間：", execution_time, "秒")
###
print("Env cost:",env.total_cost)
# -------------------------------------------------------------
import matplotlib.pyplot as plt
plt.rcParams.update({'font.size': 22})

def plot_pile(car_id, data):
    title = car_id
    plot_time = np.array(range(96))
    plot_pile_price = data["Price"]
    plot_pile_soc   = data["SOC"][car_id]
    plot_pile_soc_T = data["SOC_T"][car_id]
    plot_pile_P_t   = data["P_action"][car_id]
    plot_pile_P_L   = data["P_lower"][car_id]
    plot_pile_P_U   = data["P_upper"][car_id]

    if len(plot_pile_soc) < 96:
        plot_pile_soc   = np.concatenate( (  plot_pile_soc, np.zeros(96 - len(plot_pile_soc)) ) )

    if len(plot_pile_soc_T) < 96:
        plot_pile_soc_T = np.concatenate( (plot_pile_soc_T, np.zeros(96 - len(plot_pile_soc_T)) ) )

    if len(plot_pile_P_t) < 96:
        plot_pile_P_t   = np.concatenate( (  plot_pile_P_t, np.zeros(96 - len(plot_pile_P_t)) ) )

    if len(plot_pile_P_L) < 96:
        plot_pile_P_L   = np.concatenate( (  plot_pile_P_L, np.zeros(96 - len(plot_pile_P_L)) ) )

    if len(plot_pile_P_U) < 96:
        plot_pile_P_U   = np.concatenate( (  plot_pile_P_U, np.zeros(96 - len(plot_pile_P_U)) ) )

    plt.rcParams["figure.figsize"] = (20, 8)
    plt.rcParams['font.family'] = 'serif'
    plt.rcParams['font.serif']  = ['Times New Roman'] + plt.rcParams['font.serif']

    fig,axes = plt.subplots()
    plt.title(title)
    axes.set_xticks(plot_time[::5])
    axes.set_xlabel('Time Step')
    
    # price
    axes.set_ylim(1,8)
    axes.set_ylabel('Price (TWD)', color='steelblue')
    axes.spines['right'].set_position(("axes",1))
    axes.tick_params(axis='y', color='steelblue')
    axes.plot( plot_time, plot_pile_price, label = "Random Electricity Price", linewidth = 4, color='steelblue')

    # action
    sub_action = axes.twinx()
    sub_action.set_ylabel('Action')
    sub_action.spines['right'].set_position(("axes",1.1))
    sub_action.set_ylim(-1.5,1.5)
    
    sub_action.plot( plot_time, plot_pile_P_t, label = "P_t", color = 'green', linewidth = 4 )
    sub_action.fill_between(plot_time, plot_pile_P_L, plot_pile_P_U, alpha = 0.3,color = 'green')

    # soc
    sub_soc = axes.twinx()
    sub_soc.set_ylabel('SOC (%)',color='red')
    sub_soc.set_ylim(0,100)
    sub_soc.spines['right'].set_position(("axes",1))
    sub_soc.tick_params(axis='y',colors = 'red')
    sub_soc.plot( plot_time, np.array(plot_pile_soc_T)*100, label = "Target SOC", color = 'darkgray', linewidth = 4 )
    sub_soc.plot( plot_time,   np.array(plot_pile_soc)*100, label = "SOC"       , color = 'red'     , linewidth = 4 )

    # set all legend    
    fig.legend(bbox_to_anchor=(0.5, -0.06), loc="lower center", fontsize='small', shadow=False, ncol=6)
    fig.show()

    #save img
    desired_dpi = 300
    # fig.savefig("plot/tw/"+ title + '.svg', dpi=desired_dpi, bbox_inches='tight')
    
def plot_station(data):
    title = "Power Usage"
    plot_time = np.array(range(96))
    plot_pile_price = data["Price"]
    plot_P_total    = data["P_total"]
    plot_P_max_station = data["P_max_station"]
    
    if len(plot_P_total) < 96:
        plot_P_total = np.concatenate( (  plot_P_total, np.zeros(96 - len(plot_P_total)) ) )
    
    plt.rcParams["figure.figsize"] = (20, 8)
    plt.rcParams['font.family'] = 'serif'
    plt.rcParams['font.serif']  = ['Times New Roman'] + plt.rcParams['font.serif']

    fig,axes = plt.subplots()
    plt.title(title)
    axes.set_xticks(plot_time[::5])
    axes.set_xlabel('Time Step')
    
    # power
    axes.set_ylabel('Power(kW)')
    axes.spines['right'].set_position(("axes",1.1))
    axes.set_ylim(-(plot_P_max_station+5),plot_P_max_station+5)
    axes.bar(plot_time, plot_P_total, color = 'orange' )
    
    axes.plot( plot_time,   np.zeros(len(plot_time)) , color = 'darkgray' , linewidth = 3 )
    axes.plot( plot_time,   [plot_P_max_station]*len(plot_time), label = "P max station" , color = 'darkgray' , linewidth = 3 )
    axes.plot( plot_time,  [-plot_P_max_station]*len(plot_time), color = 'darkgray' , linewidth = 3 )

    # price
    sub_price = axes.twinx()
    sub_price.set_ylim(1,8)
    sub_price.set_ylabel('Price (TWD)', color='steelblue')
    sub_price.spines['right'].set_position(("axes",1))
    sub_price.tick_params(axis='y', color='steelblue')
    sub_price.plot( plot_time, plot_pile_price, label = "Random Electricity Price", linewidth = 4, color='steelblue')
    
    fig.legend(bbox_to_anchor=(0.5, -0.06), loc="lower center", fontsize='small', shadow=False, ncol=6)
    fig.show()

# for agent in env.possible_agents:
#     plot_pile(car_id = agent, data = env.plot_data)
    
# plot_station( data = env.plot_data)

set multi_env seed:0
{'pile_list': ['pile_20', 'pile_50', 'pile_61', 'pile_135', 'pile_147'], 'SOC': {'pile_20': 0.2, 'pile_50': 0.2, 'pile_61': 0.2, 'pile_135': 0.2833333333333333, 'pile_147': 0.21000000000000008}, 'SOC_T': {'pile_20': 0.8, 'pile_50': 0.84, 'pile_61': 0.8, 'pile_135': 0.82, 'pile_147': 0.81}, 'BC': {'pile_20': 16, 'pile_50': 24, 'pile_61': 24, 'pile_135': 75, 'pile_147': 22}, 'P_max': {'pile_20': 3.3, 'pile_50': 7.2, 'pile_61': 7.2, 'pile_135': 11.5, 'pile_147': 6.6}, 'T_d': {'pile_20': 94, 'pile_50': 70, 'pile_61': 87, 'pile_135': 44, 'pile_147': 87}, 'CE': {'pile_20': 0.9, 'pile_50': 0.9, 'pile_61': 0.9, 'pile_135': 0.9, 'pile_147': 0.9}, 'T_cur': 26, 'price': array([1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 ,
       1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 ,
       1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 , 1.9 ,
       1.9 , 1.9 , 1.9 , 4.26, 4.26, 4.26, 4.26, 4.26, 4.26, 4.26, 4.26,
       4.26, 4.26, 

In [4]:
from MILP_env import StationEnv
import numpy as np
env = StationEnv(mode = "test", N_piles = num_of_pile)
env.seed(0)

random_price = [1.81]*24+[4.13]*20+[1.81]*12+[4.13]*40

env.reset(seed = 1, select_pile = np.random.choice(env.possible_agents), price_data = random_price)

time_step = env.T_cur
###
start_time = time.time()
###
pile_data = get_pile_data(env)
print(pile_data)
charge_power = MILP_EV_real_time_scheduling(pile_data)
print("==================")

for agent in env.agent_iter():
    obs, reward, termination, truncation, info = env.last()
    if termination or truncation:
        action = None
    else:
        # action = env.action_space(agent).sample()
        action = [charge_power[agent]]

    env.step(action)
    # if time_step > 32:
    #     break
    if time_step != env.T_cur:
        pile_data = get_pile_data(env)
        print("==================")
        print(pile_data)
        charge_power = MILP_EV_real_time_scheduling(pile_data)
        time_step = env.T_cur

###
end_time = time.time()
execution_time = end_time - start_time
print("程式執行時間：", execution_time, "秒")
###
print("Env cost:",env.total_cost)

# -------------------------------------------------------------
import matplotlib.pyplot as plt
plt.rcParams.update({'font.size': 22})

def plot_pile(car_id, data):
    title = car_id
    plot_time = np.array(range(96))
    plot_pile_price = data["Price"]
    plot_pile_soc   = data["SOC"][car_id]
    plot_pile_soc_T = data["SOC_T"][car_id]
    plot_pile_P_t   = data["P_action"][car_id]
    plot_pile_P_L   = data["P_lower"][car_id]
    plot_pile_P_U   = data["P_upper"][car_id]

    if len(plot_pile_soc) < 96:
        plot_pile_soc   = np.concatenate( (  plot_pile_soc, np.zeros(96 - len(plot_pile_soc)) ) )

    if len(plot_pile_soc_T) < 96:
        plot_pile_soc_T = np.concatenate( (plot_pile_soc_T, np.zeros(96 - len(plot_pile_soc_T)) ) )

    if len(plot_pile_P_t) < 96:
        plot_pile_P_t   = np.concatenate( (  plot_pile_P_t, np.zeros(96 - len(plot_pile_P_t)) ) )

    if len(plot_pile_P_L) < 96:
        plot_pile_P_L   = np.concatenate( (  plot_pile_P_L, np.zeros(96 - len(plot_pile_P_L)) ) )

    if len(plot_pile_P_U) < 96:
        plot_pile_P_U   = np.concatenate( (  plot_pile_P_U, np.zeros(96 - len(plot_pile_P_U)) ) )

    plt.rcParams["figure.figsize"] = (20, 8)
    plt.rcParams['font.family'] = 'serif'
    plt.rcParams['font.serif']  = ['Times New Roman'] + plt.rcParams['font.serif']

    fig,axes = plt.subplots()
    plt.title(title)
    axes.set_xticks(plot_time[::5])
    axes.set_xlabel('Time Step')
    
    # price
    axes.set_ylim(1,8)
    axes.set_ylabel('Price (TWD)', color='steelblue')
    axes.spines['right'].set_position(("axes",1))
    axes.tick_params(axis='y', color='steelblue')
    axes.plot( plot_time, plot_pile_price, label = "Random Electricity Price", linewidth = 4, color='steelblue')

    # action
    sub_action = axes.twinx()
    sub_action.set_ylabel('Action')
    sub_action.spines['right'].set_position(("axes",1.1))
    sub_action.set_ylim(-1.5,1.5)
    
    sub_action.plot( plot_time, plot_pile_P_t, label = "P_t", color = 'green', linewidth = 4 )
    sub_action.fill_between(plot_time, plot_pile_P_L, plot_pile_P_U, alpha = 0.3,color = 'green')

    # soc
    sub_soc = axes.twinx()
    sub_soc.set_ylabel('SOC (%)',color='red')
    sub_soc.set_ylim(0,100)
    sub_soc.spines['right'].set_position(("axes",1))
    sub_soc.tick_params(axis='y',colors = 'red')
    sub_soc.plot( plot_time, np.array(plot_pile_soc_T)*100, label = "Target SOC", color = 'darkgray', linewidth = 4 )
    sub_soc.plot( plot_time,   np.array(plot_pile_soc)*100, label = "SOC"       , color = 'red'     , linewidth = 4 )

    # set all legend    
    fig.legend(bbox_to_anchor=(0.5, -0.06), loc="lower center", fontsize='small', shadow=False, ncol=6)
    fig.show()

    #save img
    desired_dpi = 300
    # fig.savefig("plot/tw/"+ title + '.svg', dpi=desired_dpi, bbox_inches='tight')
    
def plot_station(data):
    title = "Power Usage"
    plot_time = np.array(range(96))
    plot_pile_price = data["Price"]
    plot_P_total    = data["P_total"]
    plot_P_max_station = data["P_max_station"]
    
    if len(plot_P_total) < 96:
        plot_P_total = np.concatenate( (  plot_P_total, np.zeros(96 - len(plot_P_total)) ) )
    
    plt.rcParams["figure.figsize"] = (20, 8)
    plt.rcParams['font.family'] = 'serif'
    plt.rcParams['font.serif']  = ['Times New Roman'] + plt.rcParams['font.serif']

    fig,axes = plt.subplots()
    plt.title(title)
    axes.set_xticks(plot_time[::5])
    axes.set_xlabel('Time Step')
    
    # power
    axes.set_ylabel('Power(kW)')
    axes.spines['right'].set_position(("axes",1.1))
    axes.set_ylim(-(plot_P_max_station+5),plot_P_max_station+5)
    axes.bar(plot_time, plot_P_total, color = 'orange' )
    
    axes.plot( plot_time,   np.zeros(len(plot_time)) , color = 'darkgray' , linewidth = 3 )
    axes.plot( plot_time,   [plot_P_max_station]*len(plot_time), label = "P max station" , color = 'darkgray' , linewidth = 3 )
    axes.plot( plot_time,  [-plot_P_max_station]*len(plot_time), color = 'darkgray' , linewidth = 3 )

    # price
    sub_price = axes.twinx()
    sub_price.set_ylim(1,8)
    sub_price.set_ylabel('Price (TWD)', color='steelblue')
    sub_price.spines['right'].set_position(("axes",1))
    sub_price.tick_params(axis='y', color='steelblue')
    sub_price.plot( plot_time, plot_pile_price, label = "Random Electricity Price", linewidth = 4, color='steelblue')
    
    fig.legend(bbox_to_anchor=(0.5, -0.06), loc="lower center", fontsize='small', shadow=False, ncol=6)
    fig.show()
    

# for agent in env.possible_agents:
#     plot_pile(car_id = agent, data = env.plot_data)

# plot_station( data = env.plot_data)

set multi_env seed:0
{'pile_list': ['pile_20', 'pile_50', 'pile_61', 'pile_135', 'pile_147'], 'SOC': {'pile_20': 0.2, 'pile_50': 0.2, 'pile_61': 0.2, 'pile_135': 0.2833333333333333, 'pile_147': 0.21000000000000008}, 'SOC_T': {'pile_20': 0.8, 'pile_50': 0.84, 'pile_61': 0.8, 'pile_135': 0.82, 'pile_147': 0.81}, 'BC': {'pile_20': 16, 'pile_50': 24, 'pile_61': 24, 'pile_135': 75, 'pile_147': 22}, 'P_max': {'pile_20': 3.3, 'pile_50': 7.2, 'pile_61': 7.2, 'pile_135': 11.5, 'pile_147': 6.6}, 'T_d': {'pile_20': 94, 'pile_50': 70, 'pile_61': 87, 'pile_135': 44, 'pile_147': 87}, 'CE': {'pile_20': 0.9, 'pile_50': 0.9, 'pile_61': 0.9, 'pile_135': 0.9, 'pile_147': 0.9}, 'T_cur': 26, 'price': [1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 4.13, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81, 1.81

In [5]:
from MILP_env import StationEnv
import numpy as np
env = StationEnv(mode = "test", N_piles = num_of_pile)
env.seed(0)
random_price = [5.99]*6+[4.84]*6+[1.39]*11+[2.73]*15+[5.10]*8+[2.48]*16+[6.56]*4+[3.54]*4+[5.24]*19+[3.68]*5+[5.97]*2

env.reset(seed = 1, select_pile = np.random.choice(env.possible_agents), price_data = random_price)

time_step = env.T_cur
###
start_time = time.time()
###

pile_data = get_pile_data(env)
print(pile_data)
charge_power = MILP_EV_real_time_scheduling(pile_data)
print("==================")

for agent in env.agent_iter():
    obs, reward, termination, truncation, info = env.last()
    if termination or truncation:
        action = None
    else:
        # action = env.action_space(agent).sample()
        action = [charge_power[agent]]

    env.step(action)
    # if time_step > 32:
    #     break
    if time_step != env.T_cur:
        pile_data = get_pile_data(env)
        print("==================")
        print(pile_data)
        charge_power = MILP_EV_real_time_scheduling(pile_data)
        time_step = env.T_cur

###
end_time = time.time()
execution_time = end_time - start_time
print("程式執行時間：", execution_time, "秒")
###
print("Env cost:",env.total_cost)

# -------------------------------------------------------------
import matplotlib.pyplot as plt
plt.rcParams.update({'font.size': 22})

def plot_pile(car_id, data):
    title = car_id
    plot_time = np.array(range(96))
    plot_pile_price = data["Price"]
    plot_pile_soc   = data["SOC"][car_id]
    plot_pile_soc_T = data["SOC_T"][car_id]
    plot_pile_P_t   = data["P_action"][car_id]
    plot_pile_P_L   = data["P_lower"][car_id]
    plot_pile_P_U   = data["P_upper"][car_id]

    if len(plot_pile_soc) < 96:
        plot_pile_soc   = np.concatenate( (  plot_pile_soc, np.zeros(96 - len(plot_pile_soc)) ) )

    if len(plot_pile_soc_T) < 96:
        plot_pile_soc_T = np.concatenate( (plot_pile_soc_T, np.zeros(96 - len(plot_pile_soc_T)) ) )

    if len(plot_pile_P_t) < 96:
        plot_pile_P_t   = np.concatenate( (  plot_pile_P_t, np.zeros(96 - len(plot_pile_P_t)) ) )

    if len(plot_pile_P_L) < 96:
        plot_pile_P_L   = np.concatenate( (  plot_pile_P_L, np.zeros(96 - len(plot_pile_P_L)) ) )

    if len(plot_pile_P_U) < 96:
        plot_pile_P_U   = np.concatenate( (  plot_pile_P_U, np.zeros(96 - len(plot_pile_P_U)) ) )

    plt.rcParams["figure.figsize"] = (20, 8)
    plt.rcParams['font.family'] = 'serif'
    plt.rcParams['font.serif']  = ['Times New Roman'] + plt.rcParams['font.serif']

    fig,axes = plt.subplots()
    plt.title(title)
    axes.set_xticks(plot_time[::5])
    axes.set_xlabel('Time Step')
    
    # price
    axes.set_ylim(1,8)
    axes.set_ylabel('Price (TWD)', color='steelblue')
    axes.spines['right'].set_position(("axes",1))
    axes.tick_params(axis='y', color='steelblue')
    axes.plot( plot_time, plot_pile_price, label = "Random Electricity Price", linewidth = 4, color='steelblue')

    # action
    sub_action = axes.twinx()
    sub_action.set_ylabel('Action')
    sub_action.spines['right'].set_position(("axes",1.1))
    sub_action.set_ylim(-1.5,1.5)
    
    sub_action.plot( plot_time, plot_pile_P_t, label = "P_t", color = 'green', linewidth = 4 )
    sub_action.fill_between(plot_time, plot_pile_P_L, plot_pile_P_U, alpha = 0.3,color = 'green')

    # soc
    sub_soc = axes.twinx()
    sub_soc.set_ylabel('SOC (%)',color='red')
    sub_soc.set_ylim(0,100)
    sub_soc.spines['right'].set_position(("axes",1))
    sub_soc.tick_params(axis='y',colors = 'red')
    sub_soc.plot( plot_time, np.array(plot_pile_soc_T)*100, label = "Target SOC", color = 'darkgray', linewidth = 4 )
    sub_soc.plot( plot_time,   np.array(plot_pile_soc)*100, label = "SOC"       , color = 'red'     , linewidth = 4 )

    # set all legend    
    fig.legend(bbox_to_anchor=(0.5, -0.06), loc="lower center", fontsize='small', shadow=False, ncol=6)
    fig.show()

    #save img
    desired_dpi = 300
    # fig.savefig("plot/tw/"+ title + '.svg', dpi=desired_dpi, bbox_inches='tight')
    
def plot_station(data):
    title = "Power Usage"
    plot_time = np.array(range(96))
    plot_pile_price = data["Price"]
    plot_P_total    = data["P_total"]
    plot_P_max_station = data["P_max_station"]
    
    if len(plot_P_total) < 96:
        plot_P_total = np.concatenate( (  plot_P_total, np.zeros(96 - len(plot_P_total)) ) )
    
    plt.rcParams["figure.figsize"] = (20, 8)
    plt.rcParams['font.family'] = 'serif'
    plt.rcParams['font.serif']  = ['Times New Roman'] + plt.rcParams['font.serif']

    fig,axes = plt.subplots()
    plt.title(title)
    axes.set_xticks(plot_time[::5])
    axes.set_xlabel('Time Step')
    
    # power
    axes.set_ylabel('Power(kW)')
    axes.spines['right'].set_position(("axes",1.1))
    axes.set_ylim(-(plot_P_max_station+5),plot_P_max_station+5)
    axes.bar(plot_time, plot_P_total, color = 'orange' )
    
    axes.plot( plot_time,   np.zeros(len(plot_time)) , color = 'darkgray' , linewidth = 3 )
    axes.plot( plot_time,   [plot_P_max_station]*len(plot_time), label = "P max station" , color = 'darkgray' , linewidth = 3 )
    axes.plot( plot_time,  [-plot_P_max_station]*len(plot_time), color = 'darkgray' , linewidth = 3 )

    # price
    sub_price = axes.twinx()
    sub_price.set_ylim(1,8)
    sub_price.set_ylabel('Price (TWD)', color='steelblue')
    sub_price.spines['right'].set_position(("axes",1))
    sub_price.tick_params(axis='y', color='steelblue')
    sub_price.plot( plot_time, plot_pile_price, label = "Random Electricity Price", linewidth = 4, color='steelblue')
    
    fig.legend(bbox_to_anchor=(0.5, -0.06), loc="lower center", fontsize='small', shadow=False, ncol=6)
    fig.show()
    

# for agent in env.possible_agents:
#     plot_pile(car_id = agent, data = env.plot_data)

# plot_station( data = env.plot_data)

set multi_env seed:0
{'pile_list': ['pile_20', 'pile_50', 'pile_61', 'pile_135', 'pile_147'], 'SOC': {'pile_20': 0.2, 'pile_50': 0.2, 'pile_61': 0.2, 'pile_135': 0.2833333333333333, 'pile_147': 0.21000000000000008}, 'SOC_T': {'pile_20': 0.8, 'pile_50': 0.84, 'pile_61': 0.8, 'pile_135': 0.82, 'pile_147': 0.81}, 'BC': {'pile_20': 16, 'pile_50': 24, 'pile_61': 24, 'pile_135': 75, 'pile_147': 22}, 'P_max': {'pile_20': 3.3, 'pile_50': 7.2, 'pile_61': 7.2, 'pile_135': 11.5, 'pile_147': 6.6}, 'T_d': {'pile_20': 94, 'pile_50': 70, 'pile_61': 87, 'pile_135': 44, 'pile_147': 87}, 'CE': {'pile_20': 0.9, 'pile_50': 0.9, 'pile_61': 0.9, 'pile_135': 0.9, 'pile_147': 0.9}, 'T_cur': 26, 'price': [5.99, 5.99, 5.99, 5.99, 5.99, 5.99, 4.84, 4.84, 4.84, 4.84, 4.84, 4.84, 1.39, 1.39, 1.39, 1.39, 1.39, 1.39, 1.39, 1.39, 1.39, 1.39, 1.39, 2.73, 2.73, 2.73, 2.73, 2.73, 2.73, 2.73, 2.73, 2.73, 2.73, 2.73, 2.73, 2.73, 2.73, 2.73, 5.1, 5.1, 5.1, 5.1, 5.1, 5.1, 5.1, 5.1, 2.48, 2.48, 2.48, 2.48, 2.48, 2.48, 2.48, 